In [1]:
import numpy
import cvtda.classification

test_images = numpy.load("test_images.npy")
test_labels = numpy.load("test_labels_combined.npy")

cvtda.classification.classify(
    None, None, None, None,
    None, None, test_labels, None,
    without_diagrams = True, dump_name = "1/combined",
    catboost_device = 'CPU', xgboost_device = 'cpu',
    only_get_from_dump = True, label_names = [ "FAIL", "SUCCESS" ]
)


Trying KNeighborsClassifier - KNeighborsClassifier(n_jobs=-1, n_neighbors=50)
Got the result from ./1/combined/KNeighborsClassifier.npy
{'classifier': 'Метод k ближайших соседей', 'Accuracy': 0.79, 'AUC-ROC': 0.766478787660508, 'Precision': 0.6530797101449275, 'Recall': 0.29573420836751435, 'F1-score': 0.40711462450592883}
Trying RandomForestClassifier - RandomForestClassifier(n_jobs=-1, random_state=42)
Got the result from ./1/combined/RandomForestClassifier.npy
{'classifier': 'Случайный лес', 'Accuracy': 0.8085, 'AUC-ROC': 0.8158514171826274, 'Precision': 0.763874873864783, 'Recall': 0.31050041017227237, 'F1-score': 0.4415281423155439}
Trying HistGradientBoostingClassifier - HistGradientBoostingClassifier(max_depth=4, max_features=0.1, max_iter=20,
                               random_state=42, verbose=2)
Got the result from ./1/combined/HistGradientBoostingClassifier.npy
{'classifier': 'Град. бустинг на основе гистограмм', 'Accuracy': 0.8018, 'AUC-ROC': 0.8140625138993183, 'Precisi

classifier  Accuracy   AUC-ROC  Precision  \
0              Метод k ближайших соседей    0.7900  0.766479   0.653080   
1                          Случайный лес    0.8085  0.815851   0.763875   
2     Град. бустинг на основе гистограмм    0.8018  0.814063   0.718391   
3                               CatBoost    0.8333  0.873330   0.726631   
4                                XGBoost    0.8159  0.841579   0.695226   
5  Нейронная сеть для тополог. признаков    0.8194  0.844181   0.642214   
6                                    NaN       NaN       NaN        NaN   
7              ResNet50 – базовая модель    0.7896  0.805849   0.577819   
8         Комбинированная нейронная сеть    0.8239  0.812518   0.651319   

     Recall  F1-score  
0  0.295734  0.407115  
1  0.310500  0.441528  
2  0.307629  0.430787  
3  0.506973  0.597246  
4  0.436013  0.535921  
5  0.585316  0.612446  
6       NaN       NaN  
7  0.508614  0.541012  
8  0.597621  0.623316

In [2]:
predictions = numpy.argmax(numpy.load("1/predictions/CatBoostClassifier.npy"), axis = 1)
imgs1 = numpy.where((predictions != test_labels) & numpy.isin(test_labels, 0))[0]
imgs2 = numpy.where((predictions != test_labels) & numpy.isin(test_labels, 1))[0]
imgs3 = numpy.where((predictions == test_labels) & numpy.isin(test_labels, 0))[0]
imgs4 = numpy.where((predictions == test_labels) & numpy.isin(test_labels, 1))[0]
print(imgs1, imgs2)
len(imgs1), len(imgs2)

[   1    5    7 ... 9991 9998 9999] [  18   34   38  156  178  195  238  297  299  342  344  447  491  549
  555  565  586  589  603  611  618  627  641  657  729  759  793  811
  822  830  839  887  913  925  926  939 1031 1056 1114 1134 1190 1194
 1229 1242 1291 1330 1353 1365 1376 1414 1471 1528 1633 1657 1676 1797
 1839 1861 1981 2069 2074 2154 2280 2295 2359 2384 2389 2390 2391 2473
 2480 2532 2588 2589 2599 2652 2673 2726 2741 2747 2770 2774 2795 2804
 2811 2838 2851 2918 2924 2950 2986 3041 3085 3126 3170 3221 3251 3273
 3300 3345 3370 3380 3397 3405 3415 3469 3502 3538 3633 3671 3762 3783
 3795 3858 3894 3922 3940 3964 3997 4076 4118 4221 4241 4297 4318 4320
 4331 4339 4363 4368 4375 4396 4421 4448 4472 4490 4518 4520 4522 4548
 4564 4570 4643 4686 4687 4688 4744 4762 4782 4816 4895 4897 4937 4977
 4981 5037 5056 5089 5157 5166 5197 5209 5210 5242 5258 5290 5295 5349
 5376 5395 5427 5474 5492 5522 5555 5568 5570 5584 5606 5637 5677 5733
 5770 5859 5913 5946 5953 5962 5982 6002 

(3089, 578)

In [5]:
test_images[0].shape

(200, 200, 3)

In [18]:
import torch
import PIL.Image
import matplotlib.pyplot as plt
import torchvision.transforms.v2

figure, axes = plt.subplots(8, 10, figsize = (20, 16))

numpy.random.seed(123)

def output(img, file):
    img = torch.tensor(img).unsqueeze(0).permute((0, 3, 1, 2))
    img = torchvision.transforms.v2.Resize((48, 48), antialias = True)(img)
    img = img[0].permute((1, 2, 0)).numpy()

    os.makedirs(os.path.dirname(file), exist_ok = True)
    PIL.Image.fromarray((img * 255).astype(numpy.uint8)).save(file)

def draw(imgs, i1, i2):
    part = numpy.random.choice(imgs, size = 20)
    for i in range(10):
        axes[i1][i].imshow(test_images[part[i]])
        axes[i1][i].axis(False)
        
        axes[i2][i].imshow(test_images[part[i + 10]])
        axes[i2][i].axis(False)

        output(test_images[part[i]], f"gpt_control/{i1}/{i}.png")
        output(test_images[part[i + 10]], f"gpt_control/{i2}/{i}.png")

draw(imgs4, 0, 1)
draw(imgs2, 2, 3)
draw(imgs3, 4, 5)
draw(imgs1, 6, 7)

figure.tight_layout()

plt.savefig("1/predictions/error_examples.svg")
plt.savefig("1/predictions/error_examples.png")